# Big Data Gyak

In [1]:
from pyspark import SparkConf
from pyspark import SparkContext

conf = SparkConf()
sc = SparkContext(conf=conf)

In [ ]:
print("hello world", x)

In [2]:
sc.parallelize(range(1000)).take(5)

[0, 1, 2, 3, 4]

In [17]:
file = sc.textFile("jokt.txt").cache()

In [22]:
file.flatMap(lambda l: l.split(" "))\
.filter(lambda w: w != "")\
.map(lambda w: w.replace(":","").replace(".",""))\
.map(lambda w: (w,1))\
.reduceByKey(lambda a,b: a+b)\
.sortBy(lambda x: x[1], False)\
.take(20)

[('a', 68),
 ('az', 41),
 ('K', 17),
 ('V', 17),
 ('nem', 15),
 ('A', 14),
 ('és', 13),
 ('hogy', 13),
 ('otthoni', 13),
 ('Az', 13),
 ('vagy', 11),
 ('kell', 10),
 ('ELTE', 10),
 ('14', 8),
 ('is', 8),
 ('karanténba', 7),
 ('de', 7),
 ('egyetemi', 6),
 ('előírásai', 6),
 ('KÉRDÉSEK', 6)]

In [27]:
from functools import reduce

file.flatMap(lambda l: l.split(" "))\
.filter(lambda w: w != "")\
.map(lambda w: w.replace(":","").replace(".",""))\
.map(lambda w: (w,1))\
.groupByKey()\
.map(lambda x: (x[0], reduce(lambda a,b: a+b, x[1])))\
.take(10)


[('KÖTELEZŐ', 1),
 ('K', 17),
 ('karanténra', 1),
 ('vonatkozó', 1),
 ('egyetemi', 6),
 ('lépése', 1),
 ('előtti', 1),
 ('két', 2),
 ('hétben', 1),
 ('(pl', 4)]

In [31]:
file.flatMap(lambda l: l.split(" "))\
.filter(lambda w: w != "")\
.map(lambda w: w.replace(":","").replace(".",""))\
.map(lambda w: len(w)).max()

23

In [32]:
file.flatMap(lambda l: l.split(" "))\
.filter(lambda w: w != "")\
.map(lambda w: w.replace(":","").replace(".",""))\
.map(lambda w: (w,len(w)))\
.reduce(lambda a,b: a if a[1]>b[1] else b )

('felfüggesztés/halasztás', 23)

# Accumulator

In [38]:
elte_acc = sc.accumulator(0)
virus_acc = sc.accumulator(0)
egyetem_acc = sc.accumulator(0)

def countWords(s):
    if 'ELTE' in s.upper(): elte_acc.add(1)
    elif 'vírus' in s.lower(): virus_acc.add(1)
    elif 'egyetem' in s.lower(): egyetem_acc.add(1)
        
file.flatMap(lambda l: l.split(" "))\
.filter(lambda w: w != "")\
.map(lambda w: w.replace(":","").replace(".",""))\
.foreach(countWords)

print("ELTE",elte_acc)
print("Virus",virus_acc)
print("Egyetem",egyetem_acc)

ELTE 15
Virus 2
Egyetem 12


# Broadcast

In [41]:
brValue = ['ELTE','vírus', 'egyetem']

br_list_sc = sc.broadcast(brValue)

def found(s):
    for item in br_list_sc.value:
        if item in s:
            return True
    return False

file.flatMap(lambda l: l.split(" "))\
.filter(lambda w: w != "")\
.map(lambda w: w.replace(":","").replace(".",""))\
.filter(found)\
.take(10)

['egyetemi',
 'ELTE',
 'egyetemtől?',
 'vírus',
 'ELTE',
 'egyetemi',
 'ELTE',
 'ELTE',
 'ELTE',
 'egyetemre,']

In [42]:
from math import cos
def taketime(x):
    return cos(x)
%time taketime(2)

CPU times: total: 0 ns
Wall time: 0 ns


-0.4161468365471424

In [57]:
%time rdd1 = sc.parallelize(range(10000000)).cache()

CPU times: total: 0 ns
Wall time: 8 ms


In [58]:
%time inter = rdd1.map(taketime).cache()

CPU times: total: 0 ns
Wall time: 6 ms


In [60]:
%time print('out:',inter.reduce(lambda x,y: x+y))

out: 1.3385389790053468
CPU times: total: 0 ns
Wall time: 7.05 s


# query plan

In [61]:
res = file.flatMap(lambda l: l.split(" "))\
.filter(lambda w: w != "")\
.map(lambda w: w.replace(":","").replace(".",""))\
.map(lambda w: (w,1))\
.reduceByKey(lambda a,b: a+b)\
.sortBy(lambda x: x[1], False)

print(res.toDebugString().decode())

(2) PythonRDD[114] at RDD at PythonRDD.scala:53 []
 |  MapPartitionsRDD[113] at mapPartitions at PythonRDD.scala:145 []
 |  ShuffledRDD[112] at partitionBy at DirectMethodHandleAccessor.java:104 []
 +-(2) PairwiseRDD[111] at sortBy at C:\Users\ggombos\AppData\Local\Temp\ipykernel_3816\382939223.py:1 []
    |  PythonRDD[110] at sortBy at C:\Users\ggombos\AppData\Local\Temp\ipykernel_3816\382939223.py:1 []
    |  MapPartitionsRDD[107] at mapPartitions at PythonRDD.scala:145 []
    |  ShuffledRDD[106] at partitionBy at DirectMethodHandleAccessor.java:104 []
    +-(2) PairwiseRDD[105] at reduceByKey at C:\Users\ggombos\AppData\Local\Temp\ipykernel_3816\382939223.py:1 []
       |  PythonRDD[104] at reduceByKey at C:\Users\ggombos\AppData\Local\Temp\ipykernel_3816\382939223.py:1 []
       |  jokt.txt MapPartitionsRDD[36] at textFile at DirectMethodHandleAccessor.java:104 []
       |      CachedPartitions: 2; MemorySize: 6.7 KiB; DiskSize: 0.0 B
       |  jokt.txt HadoopRDD[35] at textFile at

In [65]:
import random
NUM_SAMPLES = 100000000

def inside(p):
    x,y = random.random(), random.random()
    return x*x + y*y < 1

count = sc.parallelize(range(NUM_SAMPLES)).filter(inside).count()

print("Pi: ",(4.0*count / NUM_SAMPLES))

Pi:  3.14149476


In [68]:
x = sc.parallelize([("hadoop",1), ("spark",1)])
y = sc.parallelize([("hadoop",2), ("spark3",2)])

joined = x.join(y)

print(joined.toDebugString().decode())


(24) PythonRDD[152] at RDD at PythonRDD.scala:53 []
 |   MapPartitionsRDD[151] at mapPartitions at PythonRDD.scala:145 []
 |   ShuffledRDD[150] at partitionBy at DirectMethodHandleAccessor.java:104 []
 +-(24) PairwiseRDD[149] at join at C:\Users\ggombos\AppData\Local\Temp\ipykernel_3816\3309303246.py:4 []
    |   PythonRDD[148] at join at C:\Users\ggombos\AppData\Local\Temp\ipykernel_3816\3309303246.py:4 []
    |   UnionRDD[147] at union at DirectMethodHandleAccessor.java:104 []
    |   PythonRDD[145] at RDD at PythonRDD.scala:53 []
    |   ParallelCollectionRDD[143] at readRDDFromFile at PythonRDD.scala:274 []
    |   PythonRDD[146] at RDD at PythonRDD.scala:53 []
    |   ParallelCollectionRDD[144] at readRDDFromFile at PythonRDD.scala:274 []


In [70]:
print(joined.collect())

[('hadoop', (1, 2))]
